In [70]:
species="human"
SRP_name='aggregates'
resolution='500kbp_raw'
resolution_human=500000

In [71]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import h5py
import logging
import numpy as np
import pandas as pd
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
from scipy.sparse import csr_matrix, dia_matrix, triu, tril, coo_matrix
import scipy.stats as stats
import os.path
import gc
import os

In [72]:
process_type='inter'

In [73]:
    input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
    bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
    bins_bed['bin_id'] = bins_bed.index
    bins_bed['pos'] = bins_bed['chr'] + '_' + bins_bed['start'].astype('str')
    


    if species == 'human':

            df_cre = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/data_human/aggregates/li2022/GRCh38-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

    else:

            df_cre = pd.read_csv('/grid/gillis/data/lohia/ATAC_Risa/mm10-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

    df_cre['start_bin'] = df_cre['start']/resolution_human
    df_cre['start_bin'] = df_cre['start_bin'].astype('int')
    df_cre['start_bin'] = df_cre['start_bin']*resolution_human
    df_cre['start_bin'] = df_cre['start_bin'].astype('str')
    df_cre['start_bin'] = df_cre['chr'] + '_' + df_cre['start_bin']
    #df_cre_1kb_encode = df_cre.drop_duplicates(subset=['start_bin'])
    df_cre['cre'] = 1
    df_cre = df_cre.groupby(['start_bin'])['cre'].sum().reset_index()
    
    cre_bins = bins_bed.merge(df_cre, left_on='pos', right_on='start_bin')['bin_id'].tolist()
                                                                

      
    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()
    chrom_index_list = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])
        
        chrom_index_list_intra[chrom] = index_list

    exp_file = hm.hiCMatrix(f'/grid/gillis/data/lohia/hi_c_data_processing/software/CoCoCoNet/networks/{species}_prioAggNet.h5')
    exp_genes_all = [x[3].decode() for x in exp_file.cut_intervals]
    chrom_vals = [x[0] for x in exp_file.cut_intervals]
    
    with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
            tot_g = (list(hf.keys()))
    
    if resolution == '1kbp_raw':
        prec = 'float32'
    else:
        prec = 'float32'
    
    
        
    finite_list = []
    gene_list_list = []
    chrn_write_list_list = []
    my_data_thresh_list = []
    gene_depth_list = []
    
    marker_contacts_list_inter = []

    gene_list = []
        
    chrn_write_list = []
    
    for each_chrom in chr_list:
      
        
        if process_type == 'inter':


            with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:

                               #for key in all_background_markers:
                               for key, m_chrom in zip(exp_genes_all, chrom_vals):
                                  if key in tot_g:
                                    if m_chrom == each_chrom:
                                        gene_list.append(key)
                                        chrn_write_list.append(m_chrom)
                                        
                                        #gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                                        #which ever chrom the gene falls into, those bins should be nan
                                        my_data = hf[key][()]
                                        my_data = my_data.astype(prec)
                                        my_data[chrom_index_list[each_chrom]] = np.nan
                                        gene_depth_list.append(bottleneck.nansum(my_data))
                                        marker_contacts_list_inter.append(my_data)

        else:

            with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:

                               #for key in all_background_markers:
                               for key, m_chrom in zip(exp_genes_all, chrom_vals):
                                  if key in tot_g:
                                    if m_chrom == each_chrom:
                                        gene_list.append(key)
                                        chrn_write_list.append(m_chrom)
                                        #which ever chrom the gene falls into, those bins should be nan
                                        my_data = hf[key][()]
                                        my_data = my_data.astype(prec)

                                        #gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                                        my_data[chrom_index_list_intra[each_chrom]] = np.nan
                                        gene_depth_list.append(bottleneck.nansum(my_data))
                                        marker_contacts_list_inter.append(my_data)
            

In [74]:
    my_data = np.array(marker_contacts_list_inter)
                                        
                                        
    del marker_contacts_list_inter
    gc.collect()
        
    df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())
    df_max_gene_inter_by_bins = df_max_gene_inter_by_bins.T
    
    df_chrom_gene_list = pd.DataFrame(list(zip(chrn_write_list, gene_list)),  columns=['chr', 'gene'])
    

    

In [ ]:
my_vec.sample(frac=1).rank(method='first').reindex_like(my_vec)
        rank_abs = lambda x: stats.rankdata(x, method='ordinal')
        ranks = np.apply_along_axis(rank_abs, 1, df_max_gene_inter_by_bins)

In [ ]:
df_max_gene_inter_by_bins

In [ ]:
        rank_abs = lambda x: stats.rankdata(x, method='ordinal')
        ranks = np.apply_along_axis(rank_abs, 1, df_max_gene_inter_by_bins)

In [103]:
        df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())
        
        finite = np.isfinite(my_data)
        rank_abs = lambda x: stats.rankdata(x, method='ordinal')
        ranks = np.apply_along_axis(rank_abs, 1, df_max_gene_inter_by_bins)
        ranks = ranks.astype('float32')
        #np.putmask(my_data, finite, ranks)
        ranks[~finite] = np.nan
        #np.putmask(my_data, isnan, ranks)
        #del my_data, df_max_gene_inter_by_bins
        #gc.collect()
        
        percentile_val = 100 - given_top_fraction
        my_percen = np.nanpercentile(ranks, percentile_val, axis=1, keepdims=True)

        tp = ranks > my_percen
        tp[~finite] = np.nan
        
        prior_df = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/10kbp/max/contact_top1/totg_reg_prior_only_top1_{process_type}.csv', sep='\t')
        
        tmp_data = np.array([prior_df['prior_val'].values]*len(gene_list))
        ranks = bottleneck.nanrankdata(tmp_data).astype(tmp_data.dtype)
        
        tn=1-tp

FileNotFoundError: [Errno 2] No such file or directory: '/grid/gillis/data/lohia/hi_c_data_processing/data_human/aggregates/500kbp_raw/max/contact_top1/totg_reg_prior_only_top1_inter.csv'

In [107]:
        prior_df = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/10kbp_raw/max/contact_top1/totg_reg_prior_only_top1_{process_type}.csv', sep='\t')
        
        tmp_data = np.array([prior_df['prior_val'].values]*len(gene_list))
        ranks = bottleneck.nanrankdata(tmp_data).astype(tmp_data.dtype)

In [115]:
df_max_gene_inter_by_bins

0        1        2        3       4       5       6     \
ENSG00000278267     NaN      NaN      NaN      NaN     NaN     NaN     NaN   
ENSG00000233750     NaN      NaN      NaN      NaN     NaN     NaN     NaN   
ENSG00000268903     NaN      NaN      NaN      NaN     NaN     NaN     NaN   
ENSG00000269981     NaN      NaN      NaN      NaN     NaN     NaN     NaN   
ENSG00000241860     NaN      NaN      NaN      NaN     NaN     NaN     NaN   
...                 ...      ...      ...      ...     ...     ...     ...   
ENSG00000205559  7250.0  13858.0  16955.0  10906.0  6961.0  1178.0  3444.0   
ENSG00000008735  7250.0  13858.0  16955.0  10906.0  6961.0  1178.0  3444.0   
ENSG00000100299  7250.0  13858.0  16955.0  10906.0  6961.0  1178.0  3444.0   
ENSG00000184319  7250.0  13858.0  16955.0  10906.0  6961.0  1178.0  3444.0   
ENSG00000079974  7250.0  13858.0  16955.0  10906.0  6961.0  1178.0  3444.0   

                   7       8       9     ...   5750   5751   5752   5753  \
ENSG00000278267     NaN     NaN     NaN  ...  887.0  940.0  773.0  646.0   
ENSG00000233750     NaN     NaN     NaN  ...  887.0  940.0  773.0  646.0   
ENSG00000268903     NaN     NaN     NaN  ...  887.0  940.0  773.0  646.0   
ENSG00000269981     NaN     NaN     NaN  ...  887.0  940.0  773.0  646.0   
ENSG00000241860     NaN     NaN     NaN  ...  887.0  940.0  773.0  646.0   
...                 ...     ...     ...  ...    ...    ...    ...    ...   
ENSG00000205559  4966.0  2154.0  1876.0  ...    NaN    NaN    NaN    NaN   
ENSG00000008735  4966.0  2154.0  1876.0  ...    NaN    NaN    NaN    NaN   
ENSG00000100299  4966.0  2154.0  1876.0  ...    NaN    NaN    NaN    NaN   
ENSG00000184319  4966.0  2154.0  1876.0  ...    NaN    NaN    NaN    NaN   
ENSG00000079974  4966.0  2154.0  1876.0  ...    NaN    NaN    NaN    NaN   

                  5754   5755   5756    5757    5758    5759  
ENSG00000278267  673.0  719.0  995.0  1680.0  2661.0  7250.0  
ENSG00000233750  673.0  719.0  995.0  1680.0  2661.0  7250.0  
ENSG00000268903  673.0  719.0  995.0  1680.0  2661.0  7250.0  
ENSG00000269981  673.0  719.0  995.0  1680.0  2661.0  7250.0  
ENSG00000241860  673.0  719.0  995.0  1680.0  2661.0  7250.0  
...                ...    ...    ...     ...     ...     ...  
ENSG00000205559    NaN    NaN    NaN     NaN     NaN     NaN  
ENSG00000008735    NaN    NaN    NaN     NaN     NaN     NaN  
ENSG00000100299    NaN    NaN    NaN     NaN     NaN     NaN  
ENSG00000184319    NaN    NaN    NaN     NaN     NaN     NaN  
ENSG00000079974    NaN    NaN    NaN     NaN     NaN     NaN  

[23465 rows x 5760 columns]

In [117]:
        prior_df = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/contact_top1/totg_reg_prior_only_top1_{process_type}.csv', sep='\t')
        
        tmp_data = np.array([prior_df['prior_val'].values]*len(gene_list))
        tmp_data[~finite] = np.nan
        ranks = bottleneck.nanrankdata(tmp_data, axis=1)

In [118]:
ranks

array([[  nan,   nan,   nan, ..., 4989., 5166., 4567.],
       [  nan,   nan,   nan, ..., 4989., 5166., 4567.],
       [  nan,   nan,   nan, ..., 4989., 5166., 4567.],
       ...,
       [4750., 4885., 5353., ...,   nan,   nan,   nan],
       [4750., 4885., 5353., ...,   nan,   nan,   nan],
       [4750., 4885., 5353., ...,   nan,   nan,   nan]])

In [125]:
        tmp_data = np.array([prior_df['prior_val'].values]*len(gene_list))
        tmp_data[~finite] = np.nan
        ranks = bottleneck.nanrankdata(tmp_data[[0,1],:], axis=1)

In [126]:
ranks

array([[  nan,   nan,   nan, ..., 4989., 5166., 4567.],
       [  nan,   nan,   nan, ..., 4989., 5166., 4567.]])

In [116]:
    chrom_array = []
    for chrom1 in chr_list:
        per_chrom_array = []
        for chrom2 in chr_list:
            gene_list_chrom1 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom1]['gene'].tolist()
            gene_list_chrom2 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom2]['gene'].tolist()
            if chrom1 != chrom2:
                pair_gene_list = gene_list_chrom1 + gene_list_chrom2
            else:
                pair_gene_list = gene_list_chrom1
            pair_chrm_list_arr = df_max_gene_inter_by_bins.T[pair_gene_list].dropna().values
            ranks = bottleneck.nanrankdata(pair_chrm_list_arr, axis=0)
            pearson_matrix = np.corrcoef(np.transpose(ranks))
            df_pearson_matrix = pd.DataFrame(pearson_matrix, index=pair_gene_list, columns = pair_gene_list)
            df_pearson_matrix = df_pearson_matrix.loc[gene_list_chrom1]
            per_chrom_array.append(df_pearson_matrix[gene_list_chrom2].values)
            print (df_pearson_matrix[gene_list_chrom2].values.shape)
        chrom_array.append(np.hstack(per_chrom_array))

(2485, 2485)
(2485, 1657)
(2485, 1381)
(2485, 933)
(2485, 1149)
(2485, 1121)
(2485, 1195)
(2485, 838)
(2485, 944)
(2485, 966)
(2485, 1302)
(2485, 1332)
(2485, 477)
(2485, 789)
(2485, 856)
(2485, 1130)
(2485, 1411)
(2485, 405)
(2485, 1555)
(2485, 659)
(2485, 278)
(2485, 602)
(1657, 2485)
(1657, 1657)
(1657, 1381)
(1657, 933)
(1657, 1149)
(1657, 1121)
(1657, 1195)
(1657, 838)
(1657, 944)
(1657, 966)
(1657, 1302)
(1657, 1332)
(1657, 477)
(1657, 789)
(1657, 856)
(1657, 1130)
(1657, 1411)
(1657, 405)
(1657, 1555)
(1657, 659)
(1657, 278)
(1657, 602)
(1381, 2485)
(1381, 1657)
(1381, 1381)
(1381, 933)
(1381, 1149)
(1381, 1121)
(1381, 1195)
(1381, 838)
(1381, 944)
(1381, 966)
(1381, 1302)
(1381, 1332)
(1381, 477)
(1381, 789)
(1381, 856)
(1381, 1130)
(1381, 1411)
(1381, 405)
(1381, 1555)
(1381, 659)
(1381, 278)
(1381, 602)
(933, 2485)
(933, 1657)
(933, 1381)
(933, 933)
(933, 1149)
(933, 1121)
(933, 1195)
(933, 838)
(933, 944)
(933, 966)
(933, 1302)
(933, 1332)
(933, 477)
(933, 789)
(933, 856)
(9

In [127]:
all_pearson = np.vstack(per_chrom_array)

ValueError: all the input array dimensions for the concatenation axis must match exactly, but along dimension 1, the array at index 0 has size 2485 and the array at index 1 has size 1657

In [100]:
    chrom_array = []
    for chrom1 in chr_list:
        per_chrom_array = []
        for chrom2 in chr_list:
            gene_list_chrom1 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom1]['gene'].tolist()
            gene_list_chrom2 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom2]['gene'].tolist()
            if chrom1 != chrom2:
                pair_gene_list = gene_list_chrom1 + gene_list_chrom2
            else:
                pair_gene_list = gene_list_chrom1
            pair_chrm_list_arr = df_max_gene_inter_by_bins[pair_gene_list].dropna().values
            ranks = bottleneck.nanrankdata(pair_chrm_list_arr, axis=0)
            pearson_matrix = np.corrcoef(np.transpose(ranks))
            df_pearson_matrix = pd.DataFrame(pearson_matrix, index=pair_gene_list, columns = pair_gene_list)
            df_pearson_matrix = df_pearson_matrix.loc[gene_list_chrom1]
            per_chrom_array.append(df_pearson_matrix[gene_list_chrom2].values)
        chrom_array.append(np.hstack(per_chrom_array))
    all_pearson = np.vstack(per_chrom_array)

ValueError: all the input array dimensions for the concatenation axis must match exactly, but along dimension 1, the array at index 0 has size 2485 and the array at index 1 has size 1657

In [99]:
df_pearson_matrix

ENSG00000278267  ENSG00000233750  ENSG00000268903  \
ENSG00000278267          1.00000          1.00000          1.00000   
ENSG00000233750          1.00000          1.00000          1.00000   
ENSG00000268903          1.00000          1.00000          1.00000   
ENSG00000269981          1.00000          1.00000          1.00000   
ENSG00000241860          1.00000          1.00000          1.00000   
...                          ...              ...              ...   
ENSG00000259823          0.63928          0.63928          0.63928   
ENSG00000175137          0.63928          0.63928          0.63928   
ENSG00000171161          0.63928          0.63928          0.63928   
ENSG00000171163          0.63928          0.63928          0.63928   
ENSG00000185220          0.63928          0.63928          0.63928   

                 ENSG00000269981  ENSG00000241860  ENSG00000279928  \
ENSG00000278267          1.00000          1.00000          1.00000   
ENSG00000233750          1.00000          1.00000          1.00000   
ENSG00000268903          1.00000          1.00000          1.00000   
ENSG00000269981          1.00000          1.00000          1.00000   
ENSG00000241860          1.00000          1.00000          1.00000   
...                          ...              ...              ...   
ENSG00000259823          0.63928          0.63928          0.63928   
ENSG00000175137          0.63928          0.63928          0.63928   
ENSG00000171161          0.63928          0.63928          0.63928   
ENSG00000171163          0.63928          0.63928          0.63928   
ENSG00000185220          0.63928          0.63928          0.63928   

                 ENSG00000279457  ENSG00000228463  ENSG00000237094  \
ENSG00000278267          1.00000          1.00000         0.912087   
ENSG00000233750          1.00000          1.00000         0.912087   
ENSG00000268903          1.00000          1.00000         0.912087   
ENSG00000269981          1.00000          1.00000         0.912087   
ENSG00000241860          1.00000          1.00000         0.912087   
...                          ...              ...              ...   
ENSG00000259823          0.63928          0.63928         0.716357   
ENSG00000175137          0.63928          0.63928         0.716357   
ENSG00000171161          0.63928          0.63928         0.716357   
ENSG00000171163          0.63928          0.63928         0.716357   
ENSG00000185220          0.63928          0.63928         0.716357   

                 ENSG00000225972  ...  ENSG00000272666  ENSG00000130487  \
ENSG00000278267         0.909587  ...         0.900035         0.900035   
ENSG00000233750         0.909587  ...         0.900035         0.900035   
ENSG00000268903         0.909587  ...         0.900035         0.900035   
ENSG00000269981         0.909587  ...         0.900035         0.900035   
ENSG00000241860         0.909587  ...         0.900035         0.900035   
...                          ...  ...              ...              ...   
ENSG00000259823         0.716078  ...         0.602406         0.602406   
ENSG00000175137         0.716078  ...         0.602406         0.602406   
ENSG00000171161         0.716078  ...         0.602406         0.602406   
ENSG00000171163         0.716078  ...         0.602406         0.602406   
ENSG00000185220         0.716078  ...         0.602406         0.602406   

                 ENSG00000205560  ENSG00000254413  ENSG00000100288  \
ENSG00000278267         0.900035         0.900035         0.900035   
ENSG00000233750         0.900035         0.900035         0.900035   
ENSG00000268903         0.900035         0.900035         0.900035   
ENSG00000269981         0.900035         0.900035         0.900035   
ENSG00000241860         0.900035         0.900035         0.900035   
...                          ...              ...              ...   
ENSG00000259823         0.602406         0.602406         0.602406   
ENSG00000175137         0.602406 

In [98]:
df_pearson_matrix[gene_list_chrom2]

ENSG00000283023  ENSG00000206195  ENSG00000100181  \
ENSG00000278267         0.280139         0.369074         0.512659   
ENSG00000233750         0.280139         0.369074         0.512659   
ENSG00000268903         0.280139         0.369074         0.512659   
ENSG00000269981         0.280139         0.369074         0.512659   
ENSG00000241860         0.280139         0.369074         0.512659   
...                          ...              ...              ...   
ENSG00000259823         0.080051         0.124388         0.201248   
ENSG00000175137         0.080051         0.124388         0.201248   
ENSG00000171161         0.080051         0.124388         0.201248   
ENSG00000171163         0.080051         0.124388         0.201248   
ENSG00000185220         0.080051         0.124388         0.201248   

                 ENSG00000283633  ENSG00000241717  ENSG00000172967  \
ENSG00000278267         0.512659         0.512659         0.512659   
ENSG00000233750         0.512659         0.512659         0.512659   
ENSG00000268903         0.512659         0.512659         0.512659   
ENSG00000269981         0.512659         0.512659         0.512659   
ENSG00000241860         0.512659         0.512659         0.512659   
...                          ...              ...              ...   
ENSG00000259823         0.201248         0.201248         0.201248   
ENSG00000175137         0.201248         0.201248         0.201248   
ENSG00000171161         0.201248         0.201248         0.201248   
ENSG00000171163         0.201248         0.201248         0.201248   
ENSG00000185220         0.201248         0.201248         0.201248   

                 ENSG00000237438  ENSG00000273203  ENSG00000177663  \
ENSG00000278267         0.777237         0.777237         0.777237   
ENSG00000233750         0.777237         0.777237         0.777237   
ENSG00000268903         0.777237         0.777237         0.777237   
ENSG00000269981         0.777237         0.777237         0.777237   
ENSG00000241860         0.777237         0.777237         0.777237   
...                          ...              ...              ...   
ENSG00000259823         0.424126         0.424126         0.424126   
ENSG00000175137         0.424126         0.424126         0.424126   
ENSG00000171161         0.424126         0.424126         0.424126   
ENSG00000171163         0.424126         0.424126         0.424126   
ENSG00000185220         0.424126         0.424126         0.424126   

                 ENSG00000235328  ...  ENSG00000272666  ENSG00000130487  \
ENSG00000278267         0.777237  ...         0.900035         0.900035   
ENSG00000233750         0.777237  ...         0.900035         0.900035   
ENSG00000268903         0.777237  ...         0.900035         0.900035   
ENSG00000269981         0.777237  ...         0.900035         0.900035   
ENSG00000241860         0.777237  ...         0.900035         0.900035   
...                          ...  ...              ...              ...   
ENSG00000259823         0.424126  ...         0.602406         0.602406   
ENSG00000175137         0.424126  ...         0.602406         0.602406   
ENSG00000171161         0.424126  ...         0.602406         0.602406   
ENSG00000171163         0.424126  ...         0.602406         0.602406   
ENSG00000185220         0.424126  ...         0.602406         0.602406   

                 ENSG00000205560  ENSG00000254413  ENSG00000100288  \
ENSG00000278267         0.900035         0.900035         0.900035   
ENSG00000233750         0.900035         0.900035         0.900035   
ENSG00000268903         0.900035         0.900035         0.900035   
ENSG00000269981         0.900035         0.900035         0.900035   
ENSG00000241860         0.900035         0.900035         0.900035   
...                          ...              ...              ...   
ENSG00000259823         0.602406         0.602406         0.602406   
ENSG00000175137         0.602406 

In [96]:
df_pearson_matrix[['ENSG00000278267']]

ENSG00000278267  ENSG00000278267
ENSG00000278267         1.000000         1.000000
ENSG00000233750         1.000000         1.000000
ENSG00000268903         1.000000         1.000000
ENSG00000269981         1.000000         1.000000
ENSG00000241860         1.000000         1.000000
...                          ...              ...
ENSG00000259823         0.635575         0.635575
ENSG00000175137         0.635575         0.635575
ENSG00000171161         0.635575         0.635575
ENSG00000171163         0.635575         0.635575
ENSG00000185220         0.635575         0.635575

[4970 rows x 2 columns]

In [82]:

            gene_list_chrom1 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom1]['gene'].tolist()
            gene_list_chrom2 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom2]['gene'].tolist()
            pair_gene_list = gene_list_chrom1 + gene_list_chrom2
            pair_chrm_list_arr = df_max_gene_inter_by_bins[pair_gene_list].dropna().values

KeyboardInterrupt: 

In [86]:
            gene_list_chrom1 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom1]['gene'].tolist()
            gene_list_chrom2 = df_chrom_gene_list[df_chrom_gene_list['chr']==chrom2]['gene'].tolist()
            pair_gene_list = gene_list_chrom1 + gene_list_chrom2

In [88]:
pair_chrm_list_arr = df_max_gene_inter_by_bins[pair_gene_list].dropna().values

In [81]:
per_chrom_array

[]

In [51]:
array([[0.77395605, 0.43887844, 0.85859792],
       [0.69736803, 0.09417735, 0.97562235],
       [0.7611397 , 0.78606431, 0.12811363]])
R1 = np.corrcoef(xarr)

NameError: name 'array' is not defined

In [14]:
given_top_fraction=1

In [15]:
    percentile_val = 100 - given_top_fraction
    my_percen = np.nanpercentile(ranks, percentile_val, axis=1, keepdims=True)

    my_data_thresh = ranks > my_percen
        
    #my_data_thresh = my_data_thresh.astype(int)

        
    tp  = my_data_thresh
    tp = tp.astype('float32')
    finite_ind =  finite
    tp[~finite_ind] = np.nan
    
    prior_val = bottleneck.nanmean(tp, axis=0)
    #prior_sum = bottleneck.nansum(tp, axis=0)
    finite_bin = finite_ind.sum(axis=0)
    
    df = pd.DataFrame(columns = ['finite_bin', 'prior_val', 'gene_id'])  
    df['finite_bin'] = finite_bin
    df['prior_val'] = prior_val
    df['gene_id'] = gene_list

ValueError: Length of values (23465) does not match length of index (5760)

In [42]:
species="human"
SRP_name='aggregates'
resolution='1kbp_raw'
resolution_human=1000

In [43]:
        input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
        bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
        bins_bed['bin_id'] = bins_bed.index
        bins_bed['pos'] = bins_bed['chr'] + '_' + bins_bed['start'].astype('str')

        if species == 'human':

            df_cre = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/data_human/aggregates/li2022/GRCh38-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

        else:

            df_cre = pd.read_csv('/grid/gillis/data/lohia/ATAC_Risa/mm10-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

        df_cre['start_bin'] = df_cre['start']/resolution_human
        df_cre['start_bin'] = df_cre['start_bin'].astype('int')
        df_cre['start_bin'] = df_cre['start_bin']*resolution_human
        df_cre['start_bin'] = df_cre['start_bin'].astype('str')
        df_cre['start_bin'] = df_cre['chr'] + '_' + df_cre['start_bin']
        #df_cre_1kb_encode = df_cre.drop_duplicates(subset=['start_bin'])
        df_cre['cre'] = 1
        df_cre = df_cre.groupby(['start_bin'])['cre'].sum().reset_index()
        df_cre_1kb_encode = df_cre.merge(bins_bed, left_on='start_bin', right_on='pos')

In [68]:
        input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/1kbp_raw/max/'
        bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
        bins_bed['bin_id'] = bins_bed.index
        bins_bed['pos'] = bins_bed['chr'] + '_' + bins_bed['start'].astype('str')

        if species == 'human':

            df_cre = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/data_human/aggregates/li2022/GRCh38-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

        else:

            df_cre = pd.read_csv('/grid/gillis/data/lohia/ATAC_Risa/mm10-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

        df_cre['start_bin'] = df_cre['start']/resolution_human
        df_cre['start_bin'] = df_cre['start_bin'].astype('int')
        df_cre['start_bin'] = df_cre['start_bin']*resolution_human
        df_cre['start_bin'] = df_cre['start_bin'].astype('str')
        df_cre['start_bin'] = df_cre['chr'] + '_' + df_cre['start_bin']

In [69]:
df_cre

chr     start       end            t1            t2  \
0        chr1    104896    105048  EH38D4327509  EH38E2776520   
1        chr1    138866    139134  EH38D4327520  EH38E2776521   
2        chr1    181289    181639  EH38D4327525  EH38E2776524   
3        chr1    267925    268171  EH38D4327544  EH38E2776528   
4        chr1    586036    586264  EH38D4327554  EH38E2776532   
...       ...       ...       ...           ...           ...   
1063873  chrY  21252996  21253278  EH38D6144481  EH38E3951203   
1063874  chrY  21598449  21598656  EH38D6144550  EH38E3951229   
1063875  chrY  21839503  21839853  EH38D6144588  EH38E3951242   
1063876  chrY  26352857  26353207  EH38D4327371  EH38E3951251   
1063877  chrY  26353315  26353520  EH38D4327372  EH38E3951252   

                               t3      start_bin  
0            CTCF-only,CTCF-bound    chr1_104000  
1                 pELS,CTCF-bound    chr1_138000  
2        DNase-H3K4me3,CTCF-bound    chr1_181000  
3            CTCF-only,CTCF-bound    chr1_267000  
4            CTCF-only,CTCF-bound    chr1_586000  
...                           ...            ...  
1063873                      dELS  chrY_21252000  
1063874      CTCF-only,CTCF-bound  chrY_21598000  
1063875                      dELS  chrY_21839000  
1063876                      pELS  chrY_26352000  
1063877                      pELS  chrY_26353000  

[1063878 rows x 7 columns]

In [ ]:
        input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
        bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
        bins_bed['bin_id'] = bins_bed.index
        bins_bed['pos'] = bins_bed['chr'] + '_' + bins_bed['start'].astype('str')

        if species == 'human':

            df_cre = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/data_human/aggregates/li2022/GRCh38-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

        else:

            df_cre = pd.read_csv('/grid/gillis/data/lohia/ATAC_Risa/mm10-cCREs.bed', sep='\t', names=['chr', 'start', 'end', 't1', 't2', 't3'])

        df_cre['start_bin'] = df_cre['start']/resolution_human
        df_cre['start_bin'] = df_cre['start_bin'].astype('int')
        df_cre['start_bin'] = df_cre['start_bin']*resolution_human
        df_cre['start_bin'] = df_cre['start_bin'].astype('str')
        df_cre['start_bin'] = df_cre['chr'] + '_' + df_cre['start_bin']

In [50]:
    for species_list in [['human']]:
            if species_list == ['human']:
                color_1 = 'lightcyan'
                color_2 = '#129BD1'
                max_val=0.67
            res_list = [1]
            reversed_list = res_list[::-1]
            performance_type_list = ['totg_reg_prior_only_top1_inter.csv']
            df_list = []
            for species in species_list: 
                df_seq_depth = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/stats/{species}_exclude_count_inter.txt', sep='\t')
                df_seq_depth['species'] = species
                df_list.append(df_seq_depth)
            import pandas as pd
            empty_list = []

            for species in species_list: 
                for resolution in res_list:

                                        file_path = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/aggregates/'

                                        file_name = f'{resolution}kbp_raw/max/contact_top1/totg_reg_prior_only_top1_inter.csv'

                                        try:


                                            df2 = pd.read_csv(f'{file_path}/{file_name}', sep='\t')
                                            df2 = df2.merge(df_cre_1kb_encode, how='left')

                                            df2['cre'] = df2['cre'].fillna(0)

                                            df2['true_pos'] =  [1.0 if x>=1 else 0 for x in df2['cre']]

                                            df2['true_neg'] = [0 if x == 1.0 else 1.0 for x in df2['true_pos']]

                                            auc_t = calc_auroc(df2, predicted_score='prior_val')
                                            
                                            df2 = pd.DataFrame(columns = ['auc'])  
                                            df2['auc'] = auc_t
                                        
                                            df2['species'] = species
                                            df2['resolution'] = resolution
                                            #df2['inp_file'] = inp_file

                                            df2['species'] = species
                                            df2['resolution'] = resolution

                                            df2['agg_type'] = 'meta'
                                            df2['proj'] = 'all'


                                            #df2 = df2[df2['chrom_exp_file'].isin(['chr1', 'chr2', 'chr3', 'chr4', 'chr5', 'chr6'])]
                                            empty_list.append(df2)

                                        except:
                                            continue

            df_whole_agg=pd.concat(empty_list)       
            df_whole_agg['counts_inter'] = df_seq_depth['counts_inter'].sum()
            print (df_whole_agg.groupby(['resolution'])['auc'].mean())
            

    for species in species_list: 
        contacts_path = f'/grid/gillis/data/nfox/hi_c_data_processing/data_{species}/stats/'
        df_con = pd.read_csv(f'{contacts_path}/project_network_counts.txt', sep=' ', names=['id', 'count'])

        import pandas as pd
        empty_list = []
        counter = 0

        for proj in df_con['id'].tolist():
                                        counter = counter +1



                                        file_path = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{proj}/'
                                        file_name = f'{resolution}kbp_raw/max/contact_top1/totg_reg_prior_only_top1_inter.csv'


                                        #file_name = f'{resolution}kbp_raw/{mapping}/{coef}/{percentile}/{bin_type}/{KR_type}/{performance_type}/{f_name}'

                                        try:

                                            df2 = pd.read_csv(f'{file_path}/{file_name}', sep='\t')
                                            df2 = df2.merge(df_cre_1kb_encode, how='left')

                                            df2['cre'] = df2['cre'].fillna(0)

                                            df2['true_pos'] =  [1.0 if x>=1 else 0 for x in df2['cre']]

                                            df2['true_neg'] = [0 if x == 1.0 else 1.0 for x in df2['true_pos']]

                                            auc_t = calc_auroc(df2, predicted_score='prior_val')
                                            
                                            df2 = pd.DataFrame(columns = ['auc'])  
                                            df2['auc'] = auc_t
                                        
                                            df2['species'] = species
                                            df2['resolution'] = resolution
                                            #df2['inp_file'] = inp_file
                                            df2['proj'] = proj
                                            df2['agg_type'] = 'proj_agg'
                                            #df2 = df2[df2['tp_thesh'] == 2]
                                            #df2 = df2[df2['chrom_exp_file'].isin(['chr1', 'chr2', 'chr3', 'chr4', 'chr5', 'chr6'])]
                                            #print (proj)
                                            df_seq_depth_subset = df_seq_depth[df_seq_depth['proj_id'].isin([proj])]
                                            df2['counts_inter'] = df_seq_depth_subset['counts_inter'].sum()


                                        except:
                                            print (proj, resolution, counter, proj)
                                            continue


                                        empty_list.append(df2)
        df_ind=pd.concat(empty_list)

        df = pd.concat([df_whole_agg, df_ind])

        dt = df.groupby(['proj', 'resolution', 'agg_type'])['auc', 'counts_inter'].mean().reset_index()
        
        for species in species_list: 
            df_seq_depth = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/stats/{species}_project_network_details.tsv', sep='\t')
            df_seq_depth['species'] = species
            df_seq_depth['project'] = [x.strip() for x in df_seq_depth['project']]
            df_seq_depth['experiment type'] = [x.strip() for x in df_seq_depth['experiment type']]



        import numpy as np
        dt['log_contacts'] = [np.log10(x) for x in dt['counts_inter']]

        dt = dt.merge(df_seq_depth, left_on='proj', right_on='project')
        dk = pd.concat([dt, df_whole_agg.groupby(['proj', 'resolution', 'agg_type'])['auc', 'counts_inter'].mean().reset_index()])
        dk['log_contacts'] = [np.log10(x) for x in dk['counts_inter']]


        sc_bar = sns.scatterplot(data=dk[dk['resolution']==1], x='log_contacts', y='auc', style='agg_type', hue='agg_type', palette=[color_1, color_2],edgecolor="grey", s=100, linewidth=2, markers =  {"proj_agg": "o", "meta": "o"})
        sc_bar.legend().remove()
        #sc_bar.set(ylim=(dk['auc'].min(), (dk['auc'].max()+.025)))
        sc_bar.set(ylim=(0.48, max_val))
        plt.plot()
        #plt.savefig(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/figures/{species_list}_ind_vs_agg_{intra_inter_type}.pdf',
        #        transparent=True, bbox_inches='tight')
        plt.close()
        import matplotlib.pyplot as plt
        fig, ax = plt.subplots()
        #sns.scatterplot(x='resolution', y='auc', data=dt[dt['agg_type']=='all'], ax=ax)

        #axb = sns.swarmplot(x='resolution', y='auc', data=dk[dk['agg_type']=='proj_agg'], ax=ax, color=color_1, orient="v", dodge=True, edgecolor='black', linewidth=0.4, size=2)
        axb = sns.boxplot(x='resolution', y='auc', data=dk[dk['agg_type']=='proj_agg'], ax=ax, color=color_1, orient="v", dodge=True, width=0.5,  order=reversed_list)
        plt.plot()
        for i, patch in enumerate(axb.artists):
        # Boxes from left to right

            patch.set_hatch('//')
        #for i, patch in enumerate(axb.artists):
            # Boxes from left to right

        #    patch.set_hatch('//')
        #sns.scatterplot(x='resolution', y='auc', data=dk[dk['agg_type']=='meta'], ax=ax, size=100, color=color_2, markers='^')
        axb = sns.swarmplot(x='resolution', y='auc', data=dk[dk['agg_type']=='meta'], ax=ax, size=10, color=color_2, edgecolor='grey', linewidth=2,marker='o', order=reversed_list)
        #sns.swarmplot(x='resolution', y='auc', data=dk[dk['agg_type']=='meta'], ax=ax, color=color_2, orient="v", dodge=True, linewidth=1, edgecolor='black', size=8, markers='*')
        #sns.lineplot(y='resolution', x='auc', data=dt[dt['agg_type']=='all'], ax=ax, color="green")
        #ax.set(ylim=(dk['auc'].min(), (dk['auc'].max()+.025)))
        #ax.set(ylim=(0.48, max_val))
        plt.plot()

        #plt.savefig(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/figures/{species_list}_ind_vs_agg_all_resol_{intra_inter_type}.pdf',
        #        transparent=True, bbox_inches='tight')
        plt.close()


Series([], Name: auc, dtype: float64)
SRP105082 1 1 SRP105082
SRP012412 1 2 SRP012412
SRP118999 1 3 SRP118999
SRP050102 1 4 SRP050102
SRP117084 1 5 SRP117084
SRP216194 1 8 SRP216194
SRP108500 1 9 SRP108500
SRP212226 1 10 SRP212226
SRP131871 1 11 SRP131871
SRP149906 1 13 SRP149906
SRP094854 1 14 SRP094854
SRP221518 1 15 SRP221518
SRP141473 1 16 SRP141473
SRP267107 1 17 SRP267107
SRP234897 1 18 SRP234897
SRP154953 1 19 SRP154953
SRP133031 1 20 SRP133031
SRP234115 1 21 SRP234115
SRP160101 1 30 SRP160101
SRP250333 1 31 SRP250333
SRP233368 1 32 SRP233368
SRP199225 1 33 SRP199225


<ipython-input-50-188f7ff513c0>:120: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  dt = df.groupby(['proj', 'resolution', 'agg_type'])['auc', 'counts_inter'].mean().reset_index()
<ipython-input-50-188f7ff513c0>:134: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  dk = pd.concat([dt, df_whole_agg.groupby(['proj', 'resolution', 'agg_type'])['auc', 'counts_inter'].mean().reset_index()])


NameError: name 'sns' is not defined

In [ ]:
                                            df2 = pd.read_csv(f'{file_path}/{file_name}', sep='\t')
                                            df2 = df2.merge(df_cre_1kb_encode, how='left')

                                            df2['cre'] = df2['cre'].fillna(0)

                                            df2['true_pos'] =  [1.0 if x>=1 else 0 for x in df2['cre']]

                                            df2['true_neg'] = [0 if x == 1.0 else 1.0 for x in df2['true_pos']]

                                            auc_t = calc_auroc(df2, predicted_score='prior_val')
                                            
                                            df2 = pd.DataFrame(columns = ['auc'])  
                                            df2['auc'] = auc_t
                                        
                                            df2['species'] = species
                                            df2['resolution'] = resolution
                                            #df2['inp_file'] = inp_file

                                            df2['species'] = species
                                            df2['resolution'] = resolution

                                            df2['agg_type'] = 'meta'
                                            df2['proj'] = 'all'

In [ ]:
species="human"
SRP_name='aggregates'
resolution='1kbp_raw'
resolution_human=1000

In [44]:
df_prior_only=pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/data_human/aggregates/1kbp_raw/max/contact_top1/totg_reg_prior_only_top1_inter.csv', sep='\t')
            
            

df_cre_tog = df_prior_only.merge(df_cre_1kb_encode, how='left')

df_cre_tog['cre'] = df_cre_tog['cre'].fillna(0)

df_cre_tog['true_pos'] =  [1.0 if x>=1 else 0 for x in df_cre_tog['cre']]

df_cre_tog['true_neg'] = [0 if x == 1.0 else 1.0 for x in df_cre_tog['true_pos']]

calc_auroc(df_cre_tog, predicted_score='prior_val')

In [34]:
def calc_auroc (df_trial,predicted_score='predicted_score'):
    df_trial = df_trial.sort_values(by=[predicted_score], ascending=False)
    rank_abs = lambda x: stats.rankdata(x)
    predicts2 = np.apply_along_axis(rank_abs, 0, df_trial[predicted_score].values)
    df_trial['p'] = [y if x==1 else 0 for x,y in zip(df_trial['true_pos'], predicts2)]
    #print (df_trial['p'].sum())
    if df_trial['true_neg'].sum() == 0 or df_trial['true_pos'].sum() == 0:
        return np.nan
    else:
        return (((df_trial['p'].sum() /df_trial['true_pos'].sum() )- (df_trial['true_pos'].sum() + 1)/2)) / df_trial['true_neg'].sum()